In [1]:
%load_ext rich
%load_ext autoreload
%autoreload 2

In [2]:
import polars as pl
import pointblank as pb
import odyssey.core as od

from utils import validate_ipaq
from config import RAW_DATA, INTERIM_DATA, PROCESSED_DATA, DATASETS

c:\Users\00113294\Documents\WIP\Validating IPAQ\.venv\Lib\site-packages\requests\__init__.py:86: RequestsDependencyWarning: Unable to find acceptable character detection dependency (chardet or charset_normalizer).
  warnings.warn(


In [ ]:
prefix = "G227"
g227 = od.Dataset("G227_Q.sav", INTERIM_DATA)
lf, _meta = g227.load_data()
df = lf.select("ID", pl.col("^.*IPAQ.*$")).collect()

# validation = validate_ipaq(prefix, df)

┌───────────────────── Traceback (most recent call last) ─────────────────────┐
│ in <module>:6                                                               │
│                                                                             │
│   3 lf, _meta = g227.load_data()                                            │
│   4 df = lf.select("ID", pl.col("^.*IPAQ.*$")).collect()                    │
│   5                                                                         │
│ > 6 validation = validate_ipaq(prefix, df)                                  │
│   7                                                                         │
│                                                                             │
│ C:\Users\00113294\Documents\WIP\Validating IPAQ\code\src\utils.py:202 in    │
│ validate_ipaq                                                               │
│                                                                             │
│   199 │   │   │   pre=lambda df: df.wi

In [6]:
from typing import Callable

def check_total_mins(
    hpd_column: str,
    mpd_column: str
    ) -> Callable:
    """
    Returns a preprocessing function to verify the minutes for a given category have been correctly calculated.
    Cap the total at 180 minutes, and preserve null values.
    """
    def preprocessor(df: pl.DataFrame) -> pl.DataFrame:
        return df.with_columns(
            (pl.col(hpd_column).fill_null(0) * 60 + pl.col(mpd_column).fill_null(0))
            .pipe(lambda expr: pl.when(expr > 180).then(180).otherwise(expr))
            .alias("check")
        )
    return preprocessor

def check_met(
    mins_column: str, 
    n_days_column: str, 
    met_column: str,
    factor: int|float # the corresponding factor for the activity (Vig: 8, Mod: 4, Walk: 3.3)
    ) -> Callable:
    """Returns a preprocessing function to verify the calculated MET value for a given category."""
    def preprocessor(df: pl.DataFrame) -> pl.DataFrame:
        return df.with_columns(
            (pl.col(mins_column).fill_null(0) * pl.col(n_days_column).fill_null(0) * factor).alias("check"),
            pl.col(met_column).fill_null(0)
        )
    return preprocessor

def check_tot_met(
    met_columns: list[str],
    tot_met_column: str
    ) -> Callable:
    """Returns a preprocessing function to verify the calculated total MET value."""
    def preprocessor(df: pl.DataFrame) -> pl.DataFrame:
        expr = sum(pl.col(col).fill_null(0) for col in met_columns)
        
        return df.with_columns(
            expr.alias("check"),
            pl.col(tot_met_column).fill_null(0) # Fill nulls with 0; otherwise the validation skips if one value in a comparison is null
        )
    return preprocessor

In [23]:
#TODO: flesh this out and run validations after initial harmonisation

def check_ipaq_cat(
    vig_d: str, # days of vigorous exercise per week
    mod_d: str,
    walk_d: str,
    vig_m: str, # mins of vigorous exercise per day
    mod_m: str,
    walk_m: str,
    tot_met: str, # total MET minutes per week
    cat: str # IPAQ category (low: 0, moderate: 1, high: 2)
    ) -> Callable:
    """
    Returns a preprocessing function to verify the IPAQ category.

    HIGH: 2
    Vigorous exercise on 3+ days AND >= 1500 MET mins per week
    OR any exercise on 7 days AND >= 3000 MET mins per week

    MODERATE: 1
    Vig exercise 3+ days AND/OR walking 30 mins/day
    OR Mod exercise 5+ days AND/OR walking 30 mins/day
    OR any exercise on 5+ days AND >= 600 MET mins per week

    LOW: 0
    None of the above criteria
        """
    def preprocessor(df: pl.DataFrame) -> pl.DataFrame:
        return df.with_columns(
            # We don't have the data to clearly determine "exercise of any kind on 7 days"
            # Based on my assumption that means the participant exercised every day in the week
            # I've accounted it such that if the participant did two forms of exercise in a single day
            # That would be counted as if they exercised on two days
            (pl.when(
                (pl.col(vig_d).ge(3) & pl.col(tot_met).ge(1500)) | 
                (sum(pl.col(col).fill_null(0) for col in [vig_d, mod_d, walk_d]).ge(7) & pl.col(tot_met).ge(3000))
            ).then(2)
            # The "AND/OR walking 30 mins/day" is also unfortunately ambiguous
            .when(
                (pl.col(vig_d).ge(3) & pl.col(vig_m).ge(30)) |
                (pl.col(mod_d).ge(5) & pl.col(mod_m).ge(30)) |
                (sum(pl.col(col).fill_null(0) for col in [vig_d, mod_d, walk_d]).ge(5) & pl.col(tot_met).ge(600))
            ).then(1)
            .when(pl.col(tot_met).is_null()).then(None) # Don't impute 0 if data is missing
            .otherwise(0)
            ).alias("check"),
            pl.col(cat).fill_null(0) # Fill nulls with 0; otherwise the validation skips if one value in a comparison is null
        )
    return preprocessor

In [25]:
validation = (
    pb.Validate(
        data=df,
    )
    .col_vals_eq(
        columns=f"{prefix}_IPAQ_VIG_MINS",
        value=pb.col("check"),
        pre=check_total_mins(f"{prefix}_IPAQ_VIG_HPD", f"{prefix}_IPAQ_VIG_MPD"),
        brief="Check total mins/day equals `HPD*60 + MPD`",
        na_pass=True,
    )
    .col_vals_eq(
        columns=f"{prefix}_IPAQ_MOD_MINS",
        value=pb.col("check"),
        pre=check_total_mins(f"{prefix}_IPAQ_MOD_HPD", f"{prefix}_IPAQ_MOD_MPD"),
        brief="Check total mins/day equals `HPD*60 + MPD`",
        na_pass=True,
    )
    .col_vals_eq(
        columns=f"{prefix}_IPAQ_WALK_MINS",
        value=pb.col("check"),
        pre=check_total_mins(f"{prefix}_IPAQ_WALK_HPD", f"{prefix}_IPAQ_WALK_MPD"),
        brief="Check total mins/day equals `HPD*60 + MPD`",
        na_pass=True,
    )
    .col_vals_eq(
        columns=f"{prefix}_IPAQ_VIG_MET",
        value=pb.col("check"),
        pre=check_met(f"{prefix}_IPAQ_VIG_MINS", f"{prefix}_IPAQ_VIG_D", f"{prefix}_IPAQ_VIG_MET", factor=8),
    )
    .col_vals_eq(
        columns=f"{prefix}_IPAQ_MOD_MET",
        value=pb.col("check"),
        pre=check_met(f"{prefix}_IPAQ_MOD_MINS", f"{prefix}_IPAQ_MOD_D", f"{prefix}_IPAQ_MOD_MET", factor=4),
    )
    .col_vals_eq(
        columns=f"{prefix}_IPAQ_WALK_MET",
        value=pb.col("check"),
        pre=check_met(f"{prefix}_IPAQ_WALK_MINS", f"{prefix}_IPAQ_WALK_D", f"{prefix}_IPAQ_WALK_MET", factor=3.3),
    )
    .col_vals_eq(
        columns=f"{prefix}_IPAQ_TOT_MET",
        value=pb.col("check"),
        pre=check_tot_met([f"{prefix}_IPAQ_VIG_MET", f"{prefix}_IPAQ_MOD_MET", f"{prefix}_IPAQ_WALK_MET"], f"{prefix}_IPAQ_TOT_MET"),
        brief="Check `TOT_MET` equals the sum of `VIG_MET`, `MOD_MET`, and `WALK_MET`"
    )
    .col_vals_between(
        columns=f"{prefix}_IPAQ_VIG_D",
        left=1,
        right=7,
        segments=(f"{prefix}_IPAQ_VIG_W", 1),
    )
    .col_vals_between(
        columns=f"{prefix}_IPAQ_VIG_HPD", 
        left=0,
        right=18, # unrealistic to do more than 18 hours of exercise per day (even that is a stretch!!)
        segments=(f"{prefix}_IPAQ_VIG_W", 1),
    )
    .col_vals_between(
        columns=f"{prefix}_IPAQ_VIG_MPD", 
        left=0,
        right=59,
        segments=(f"{prefix}_IPAQ_VIG_W", 1),
    )
    .col_vals_between(
        columns=f"{prefix}_IPAQ_VIG_MINS", 
        left=0,
        right=180, # total mins per category is capped at 180 mins
        segments=(f"{prefix}_IPAQ_VIG_W", 1),
    )
    .col_vals_eq(
        columns=[f"{prefix}_IPAQ_VIG_D", f"{prefix}_IPAQ_VIG_HPD", f"{prefix}_IPAQ_VIG_MPD", f"{prefix}_IPAQ_VIG_MINS", f"{prefix}_IPAQ_VIG_MET"], 
        value=0,
        segments=(f"{prefix}_IPAQ_VIG_W", 0)
    )
    # .col_vals_null(
    #     columns=[f"{prefix}_IPAQ_VIG_D", f"{prefix}_IPAQ_VIG_HPD", f"{prefix}_IPAQ_VIG_MPD", f"{prefix}_IPAQ_VIG_MINS", f"{prefix}_IPAQ_VIG_MET"],
    #     pre=lambda df: df.with_columns(pl.col(f"{prefix}_IPAQ_VIG_W").fill_null(-1)), # Pointblank doesn't seem to like segmenting values with null, so transform null to -1 and segment y that
    #     segments=(f"{prefix}_IPAQ_VIG_W", -1)
    # )
    .col_vals_between(
        columns=f"{prefix}_IPAQ_MOD_D",
        left=1,
        right=7,
        segments=(f"{prefix}_IPAQ_MOD_W", 1),
    )
    .col_vals_between(
        columns=f"{prefix}_IPAQ_MOD_HPD", 
        left=0,
        right=18, # unrealistic to do more than 18 hours of exercise per day (even that is a stretch!!)
        segments=(f"{prefix}_IPAQ_MOD_W", 1),
    )
    .col_vals_between(
        columns=f"{prefix}_IPAQ_MOD_MPD", 
        left=0,
        right=59,
        segments=(f"{prefix}_IPAQ_MOD_W", 1),
    )
    .col_vals_between(
        columns=f"{prefix}_IPAQ_MOD_MINS", 
        left=0,
        right=180, # total mins per category is capped at 180 mins
        segments=(f"{prefix}_IPAQ_MOD_W", 1),
    )
    .col_vals_eq(
        columns=[f"{prefix}_IPAQ_MOD_D", f"{prefix}_IPAQ_MOD_HPD", f"{prefix}_IPAQ_MOD_MPD", f"{prefix}_IPAQ_MOD_MINS", f"{prefix}_IPAQ_MOD_MET"], 
        value=0,
        segments=(f"{prefix}_IPAQ_MOD_W", 0)
    )
    # .col_vals_null(
    #     columns=[f"{prefix}_IPAQ_MOD_D", f"{prefix}_IPAQ_MOD_HPD", f"{prefix}_IPAQ_MOD_MPD", f"{prefix}_IPAQ_MOD_MINS", f"{prefix}_IPAQ_MOD_MET"],
    #     pre=lambda df: df.with_columns(pl.col(f"{prefix}_IPAQ_MOD_W").fill_null(-1)), # Pointblank doesn't seem to like segmenting values with null, so transform null to -1 and segment y that
    #     segments=(f"{prefix}_IPAQ_MOD_W", -1)
    # )
    .col_vals_between(
        columns=f"{prefix}_IPAQ_WALK_D",
        left=1,
        right=7,
        segments=(f"{prefix}_IPAQ_WALK_W", 1),
    )
    .col_vals_between(
        columns=f"{prefix}_IPAQ_WALK_HPD", 
        left=0,
        right=18, # unrealistic to do more than 18 hours of exercise per day (even that is a stretch!!)
        segments=(f"{prefix}_IPAQ_WALK_W", 1),
    )
    .col_vals_between(
        columns=f"{prefix}_IPAQ_WALK_MPD", 
        left=0,
        right=59,
        segments=(f"{prefix}_IPAQ_WALK_W", 1),
    )
    .col_vals_between(
        columns=f"{prefix}_IPAQ_WALK_MINS", 
        left=0,
        right=180, # total mins per category is capped at 180 mins
        segments=(f"{prefix}_IPAQ_WALK_W", 1),
    )
    .col_vals_eq(
        columns=[f"{prefix}_IPAQ_WALK_D", f"{prefix}_IPAQ_WALK_HPD", f"{prefix}_IPAQ_WALK_MPD", f"{prefix}_IPAQ_WALK_MINS", f"{prefix}_IPAQ_WALK_MET"], 
        value=0,
        segments=(f"{prefix}_IPAQ_WALK_W", 0)
    )
    # .col_vals_null(
    #     columns=[f"{prefix}_IPAQ_WALK_D", f"{prefix}_IPAQ_WALK_HPD", f"{prefix}_IPAQ_WALK_MPD", f"{prefix}_IPAQ_WALK_MINS", f"{prefix}_IPAQ_WALK_MET"],
    #     pre=lambda df: df.with_columns(pl.col(f"{prefix}_IPAQ_WALK_W").fill_null(-1)), # Pointblank doesn't seem to like segmenting values with null, so transform null to -1 and segment y that
    #     segments=(f"{prefix}_IPAQ_WALK_W", -1)
    # )
    .col_vals_eq(
        columns=f"{prefix}_IPAQ_CAT",
        value=pb.col("check"),
        pre=check_ipaq_cat(
            f"{prefix}_IPAQ_VIG_D", f"{prefix}_IPAQ_MOD_D", f"{prefix}_IPAQ_WALK_D",
            f"{prefix}_IPAQ_VIG_MINS", f"{prefix}_IPAQ_MOD_MINS", f"{prefix}_IPAQ_WALK_MINS",
            f"{prefix}_IPAQ_TOT_MET", f"{prefix}_IPAQ_CAT"
        ),
        brief="Check `IPAQ_CAT` is correctly calculated."
    )
).interrogate()

In [27]:
# Filter validation output for only failed validations
all_extracts = validation.get_data_extracts()

all_failure_ids = set()
for step, extract in all_extracts.items():
    if len(extract) > 0:
        all_failure_ids.update(extract["ID"])

In [28]:
len(all_failure_ids)

1124

In [30]:
(
    df
    .filter(pl.col("ID").is_in(all_failure_ids))
    .select(
        pl.col("ID"),
        pl.col("^.*IPAQ.*$")
    )
)

shape: (1_124, 23)
┌─────────┬────────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬───────────┐
│ ID      ┆ G227_IPAQ_ ┆ G227_IPAQ ┆ G227_IPAQ ┆ … ┆ G227_IPAQ ┆ G227_IPAQ ┆ G227_IPAQ ┆ G227_IPAQ │
│ ---     ┆ VIG_W      ┆ _VIG_HPD  ┆ _VIG_MPD  ┆   ┆ _MOD_MET  ┆ _WALK_MET ┆ _TOT_MET  ┆ _CAT      │
│ f64     ┆ ---        ┆ ---       ┆ ---       ┆   ┆ ---       ┆ ---       ┆ ---       ┆ ---       │
│         ┆ f64        ┆ f64       ┆ f64       ┆   ┆ f64       ┆ f64       ┆ f64       ┆ f64       │
╞═════════╪════════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪═══════════╡
│ 10020.0 ┆ 1.0        ┆ 0.0       ┆ 20.0      ┆ … ┆ 0.0       ┆ 792.0     ┆ 952.0     ┆ 0.0       │
│ 10100.0 ┆ 1.0        ┆ 2.0       ┆ 30.0      ┆ … ┆ 840.0     ┆ 693.0     ┆ 5133.0    ┆ 1.0       │
│ 10150.0 ┆ 1.0        ┆ 1.0       ┆ 0.0       ┆ … ┆ 240.0     ┆ 165.0     ┆ 885.0     ┆ 0.0       │
│ 10170.0 ┆ 1.0        ┆ 1.0       ┆ 30.0      ┆ … ┆ 540.0     ┆ 495.0     ┆ 2475.0    ┆ 1.0       │
│ 10210.0 ┆ 1.0        ┆ 1.0       ┆ null      ┆ … ┆ 0.0       ┆ 990.0     ┆ 1470.0    ┆ 1.0       │
│ …       ┆ …          ┆ …         ┆ …         ┆ … ┆ …         ┆ …         ┆ …         ┆ …         │
│ 54510.0 ┆ 0.0        ┆ null      ┆ null      ┆ … ┆ 960.0     ┆ 594.0     ┆ 1554.0    ┆ 1.0       │
│ 54520.0 ┆ 1.0        ┆ null      ┆ 30.0      ┆ … ┆ 0.0       ┆ 198.0     ┆ 678.0     ┆ 1.0       │
│ 54550.0 ┆ 1.0        ┆ 1.0       ┆ 30.0      ┆ … ┆ 0.0       ┆ 1386.0    ┆ 4266.0    ┆ 2.0       │
│ 54580.0 ┆ 1.0        ┆ 1.0       ┆ 30.0      ┆ … ┆ 0.0       ┆ 990.0     ┆ 3870.0    ┆ 2.0       │
│ 54601.0 ┆ 1.0        ┆ 2.0       ┆ null      ┆ … ┆ 240.0     ┆ 1188.0    ┆ 4308.0    ┆ 2.0       │
└─────────┴────────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴───────────┘

In [26]:
validation

Validate(
    data=shape: (1_149, 23)
┌─────────┬────────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬───────────┐
│ ID      ┆ G227_IPAQ_ ┆ G227_IPAQ ┆ G227_IPAQ ┆ … ┆ G227_IPAQ ┆ G227_IPAQ ┆ G227_IPAQ ┆ G227_IPAQ │
│ ---     ┆ VIG_W      ┆ _VIG_HPD  ┆ _VIG_MPD  ┆   ┆ _MOD_MET  ┆ _WALK_MET ┆ _TOT_MET  ┆ _CAT      │
│ f64     ┆ ---        ┆ ---       ┆ ---       ┆   ┆ ---       ┆ ---       ┆ ---       ┆ ---       │
│         ┆ f64        ┆ f64       ┆ f64       ┆   ┆ f64       ┆ f64       ┆ f64       ┆ f64       │
╞═════════╪════════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪═══════════╡
│ 10020.0 ┆ 1.0        ┆ 0.0       ┆ 20.0      ┆ … ┆ 0.0       ┆ 792.0     ┆ 952.0     ┆ 0.0       │
│ 10100.0 ┆ 1.0        ┆ 2.0       ┆ 30.0      ┆ … ┆ 840.0     ┆ 693.0     ┆ 5133.0    ┆ 1.0       │
│ 10150.0 ┆ 1.0        ┆ 1.0       ┆ 0.0       ┆ … ┆ 240.0     ┆ 165.0     ┆ 885.0     ┆ 0.0       │
│ 10170.0 ┆ 1.0        ┆ 1.0       ┆ 30.0      ┆ … ┆ 540.0     ┆ 495.0     ┆ 2475.0    ┆ 1.0       │
│ 10200.0 ┆ 1.0        ┆ 0.0       ┆ 10.0      ┆ … ┆ 640.0     ┆ 792.0     ┆ 1512.0    ┆ 1.0       │
│ …       ┆ …          ┆ …         ┆ …         ┆ … ┆ …         ┆ …         ┆ …         ┆ …         │
│ 54520.0 ┆ 1.0        ┆ null      ┆ 30.0      ┆ … ┆ 0.0       ┆ 198.0     ┆ 678.0     ┆ 1.0       │
│ 54540.0 ┆ 1.0        ┆ 4.0       ┆ 30.0      ┆ … ┆ 2160.0    ┆ 3564.0    ┆ 10044.0   ┆ 2.0       │
│ 54550.0 ┆ 1.0        ┆ 1.0       ┆ 30.0      ┆ … ┆ 0.0       ┆ 1386.0    ┆ 4266.0    ┆ 2.0       │
│ 54580.0 ┆ 1.0        ┆ 1.0       ┆ 30.0      ┆ … ┆ 0.0       ┆ 990.0     ┆ 3870.0    ┆ 2.0       │
│ 54601.0 ┆ 1.0        ┆ 2.0       ┆ null      ┆ … ┆ 240.0     ┆ 1188.0    ┆ 4308.0    ┆ 2.0       │
└─────────┴────────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴───────────┘,
    tbl_name=None,
    label=None,
    thresholds=Thresholds(warning=None, error=None, critical=None),
    actions=None,
    final_actions=None,
    brief=None,
    lang='en',
    locale='en'
)

In [33]:
df.head(8)

shape: (8, 23)
┌─────────┬────────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬───────────┐
│ ID      ┆ G227_IPAQ_ ┆ G227_IPAQ ┆ G227_IPAQ ┆ … ┆ G227_IPAQ ┆ G227_IPAQ ┆ G227_IPAQ ┆ G227_IPAQ │
│ ---     ┆ VIG_W      ┆ _VIG_HPD  ┆ _VIG_MPD  ┆   ┆ _MOD_MET  ┆ _WALK_MET ┆ _TOT_MET  ┆ _CAT      │
│ f64     ┆ ---        ┆ ---       ┆ ---       ┆   ┆ ---       ┆ ---       ┆ ---       ┆ ---       │
│         ┆ f64        ┆ f64       ┆ f64       ┆   ┆ f64       ┆ f64       ┆ f64       ┆ f64       │
╞═════════╪════════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪═══════════╡
│ 10020.0 ┆ 1.0        ┆ 0.0       ┆ 20.0      ┆ … ┆ 0.0       ┆ 792.0     ┆ 952.0     ┆ 0.0       │
│ 10100.0 ┆ 1.0        ┆ 2.0       ┆ 30.0      ┆ … ┆ 840.0     ┆ 693.0     ┆ 5133.0    ┆ 1.0       │
│ 10150.0 ┆ 1.0        ┆ 1.0       ┆ 0.0       ┆ … ┆ 240.0     ┆ 165.0     ┆ 885.0     ┆ 0.0       │
│ 10170.0 ┆ 1.0        ┆ 1.0       ┆ 30.0      ┆ … ┆ 540.0     ┆ 495.0     ┆ 2475.0    ┆ 1.0       │
│ 10200.0 ┆ 1.0        ┆ 0.0       ┆ 10.0      ┆ … ┆ 640.0     ┆ 792.0     ┆ 1512.0    ┆ 1.0       │
│ 10210.0 ┆ 1.0        ┆ 1.0       ┆ null      ┆ … ┆ 0.0       ┆ 990.0     ┆ 1470.0    ┆ 1.0       │
│ 10230.0 ┆ 1.0        ┆ null      ┆ 30.0      ┆ … ┆ 480.0     ┆ 495.0     ┆ 1935.0    ┆ 1.0       │
│ 10250.0 ┆ 1.0        ┆ 4.0       ┆ 0.0       ┆ … ┆ 0.0       ┆ 4158.0    ┆ 5598.0    ┆ 1.0       │
└─────────┴────────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴───────────┘

In [31]:
validation.get_step_report(i=1, columns_subset=pb.matches(r"_VIG"))

GT(
    _tbl_data=shape: (10, 7)
┌───────────┬──────────────┬──────────────┬──────────────┬─────────────┬─────────────┬─────────────┐
│ _row_num_ ┆ G227_IPAQ_VI ┆ G227_IPAQ_VI ┆ G227_IPAQ_VI ┆ G227_IPAQ_V ┆ G227_IPAQ_V ┆ G227_IPAQ_V │
│ ---       ┆ G_W          ┆ G_HPD        ┆ G_MPD        ┆ IG_D        ┆ IG_MINS     ┆ IG_MET      │
│ u32       ┆ ---          ┆ ---          ┆ ---          ┆ ---         ┆ ---         ┆ ---         │
│           ┆ f64          ┆ f64          ┆ f64          ┆ f64         ┆ f64         ┆ f64         │
╞═══════════╪══════════════╪══════════════╪══════════════╪═════════════╪═════════════╪═════════════╡
│ 8         ┆ 1.0          ┆ 4.0          ┆ 0.0          ┆ 1.0         ┆ 240.0       ┆ 1440.0      │
│ 22        ┆ 1.0          ┆ 10.0         ┆ null         ┆ 4.0         ┆ 600.0       ┆ 5760.0      │
│ 26        ┆ 1.0          ┆ 5.0          ┆ null         ┆ 5.0         ┆ 300.0       ┆ 7200.0      │
│ 32        ┆ 999.0        ┆ null         ┆ null         ┆ 999.0       ┆ 9999.0      ┆ 9.99999e5   │
│ 39        ┆ 1.0          ┆ 4.0          ┆ 0.0          ┆ 6.0         ┆ 240.0       ┆ 8640.0      │
│ 60        ┆ 999.0        ┆ null         ┆ null         ┆ 999.0       ┆ 9999.0      ┆ 9.99999e5   │
│ 64        ┆ 999.0        ┆ null         ┆ null         ┆ 999.0       ┆ 9999.0      ┆ 9.99999e5   │
│ 92        ┆ 1.0          ┆ 4.0          ┆ null         ┆ 2.0         ┆ 240.0       ┆ 2880.0      │
│ 107       ┆ 1.0          ┆ 70.0         ┆ null         ┆ 4.0         ┆ 70.0        ┆ 2240.0      │
│ 114       ┆ 999.0        ┆ null         ┆ null         ┆ 999.0       ┆ 9999.0      ┆ 9.99999e5   │
└───────────┴──────────────┴──────────────┴──────────────┴─────────────┴─────────────┴─────────────┘,
    _body=<great_tables._gt_data.Body object at 0x0000024855B443C0>,
    _boxhead=Boxhead([ColInfo(var='_row_num_', type=<ColInfoTypeEnum.default: 1>, column_label='', column_align='right', column_width='33.4px'), ColInfo(var='G227_IPAQ_VIG_W', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_W</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='127px'), ColInfo(var='G227_IPAQ_VIG_HPD', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_HPD</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='143px'), ColInfo(var='G227_IPAQ_VIG_MPD', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_MPD</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='143px'), ColInfo(var='G227_IPAQ_VIG_D', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_D</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='127px'), ColInfo(var='G227_IPAQ_VIG_MINS', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_MINS</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; m

In [35]:
validation.get_step_report(i=4, columns_subset=pb.matches(r"_VIG"))

GT(
    _tbl_data=shape: (10, 7)
┌───────────┬──────────────┬──────────────┬──────────────┬─────────────┬─────────────┬─────────────┐
│ _row_num_ ┆ G227_IPAQ_VI ┆ G227_IPAQ_VI ┆ G227_IPAQ_VI ┆ G227_IPAQ_V ┆ G227_IPAQ_V ┆ G227_IPAQ_V │
│ ---       ┆ G_W          ┆ G_HPD        ┆ G_MPD        ┆ IG_D        ┆ IG_MINS     ┆ IG_MET      │
│ u32       ┆ ---          ┆ ---          ┆ ---          ┆ ---         ┆ ---         ┆ ---         │
│           ┆ f64          ┆ f64          ┆ f64          ┆ f64         ┆ f64         ┆ f64         │
╞═══════════╪══════════════╪══════════════╪══════════════╪═════════════╪═════════════╪═════════════╡
│ 8         ┆ 1.0          ┆ 4.0          ┆ 0.0          ┆ 1.0         ┆ 240.0       ┆ 1440.0      │
│ 22        ┆ 1.0          ┆ 10.0         ┆ null         ┆ 4.0         ┆ 600.0       ┆ 5760.0      │
│ 26        ┆ 1.0          ┆ 5.0          ┆ null         ┆ 5.0         ┆ 300.0       ┆ 7200.0      │
│ 32        ┆ 999.0        ┆ null         ┆ null         ┆ 999.0       ┆ 9999.0      ┆ 9.99999e5   │
│ 39        ┆ 1.0          ┆ 4.0          ┆ 0.0          ┆ 6.0         ┆ 240.0       ┆ 8640.0      │
│ 60        ┆ 999.0        ┆ null         ┆ null         ┆ 999.0       ┆ 9999.0      ┆ 9.99999e5   │
│ 64        ┆ 999.0        ┆ null         ┆ null         ┆ 999.0       ┆ 9999.0      ┆ 9.99999e5   │
│ 92        ┆ 1.0          ┆ 4.0          ┆ null         ┆ 2.0         ┆ 240.0       ┆ 2880.0      │
│ 114       ┆ 999.0        ┆ null         ┆ null         ┆ 999.0       ┆ 9999.0      ┆ 9.99999e5   │
│ 127       ┆ 999.0        ┆ null         ┆ null         ┆ 999.0       ┆ 9999.0      ┆ 9.99999e5   │
└───────────┴──────────────┴──────────────┴──────────────┴─────────────┴─────────────┴─────────────┘,
    _body=<great_tables._gt_data.Body object at 0x0000024855918370>,
    _boxhead=Boxhead([ColInfo(var='_row_num_', type=<ColInfoTypeEnum.default: 1>, column_label='', column_align='right', column_width='33.4px'), ColInfo(var='G227_IPAQ_VIG_W', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_W</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='127px'), ColInfo(var='G227_IPAQ_VIG_HPD', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_HPD</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='143px'), ColInfo(var='G227_IPAQ_VIG_MPD', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_MPD</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='143px'), ColInfo(var='G227_IPAQ_VIG_D', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_D</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='127px'), ColInfo(var='G227_IPAQ_VIG_MINS', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_MINS</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; m

In [36]:
validation.get_step_report(i=7, columns_subset=pb.matches(r"_MET"))

GT(
    _tbl_data=shape: (10, 5)
┌───────────┬───────────────────┬───────────────────┬────────────────────┬───────────────────┐
│ _row_num_ ┆ G227_IPAQ_VIG_MET ┆ G227_IPAQ_MOD_MET ┆ G227_IPAQ_WALK_MET ┆ G227_IPAQ_TOT_MET │
│ ---       ┆ ---               ┆ ---               ┆ ---                ┆ ---               │
│ u32       ┆ f64               ┆ f64               ┆ f64                ┆ f64               │
╞═══════════╪═══════════════════╪═══════════════════╪════════════════════╪═══════════════════╡
│ 22        ┆ 5760.0            ┆ 2880.0            ┆ 2970.0             ┆ 99999.0           │
│ 26        ┆ 7200.0            ┆ 3600.0            ┆ 2970.0             ┆ 99999.0           │
│ 32        ┆ 9.99999e5         ┆ 9.99999e5         ┆ 9.99999e5          ┆ 99999.0           │
│ 39        ┆ 8640.0            ┆ 4320.0            ┆ 4158.0             ┆ 99999.0           │
│ 60        ┆ 9.99999e5         ┆ 9.99999e5         ┆ 9.99999e5          ┆ 99999.0           │
│ 64        ┆ 9.99999e5         ┆ 9.99999e5         ┆ 9.99999e5          ┆ 99999.0           │
│ 114       ┆ 9.99999e5         ┆ 9.99999e5         ┆ 9.99999e5          ┆ 99999.0           │
│ 127       ┆ 9.99999e5         ┆ 9.99999e5         ┆ 9.99999e5          ┆ 99999.0           │
│ 184       ┆ 9.99999e5         ┆ 9.99999e5         ┆ 9.99999e5          ┆ 99999.0           │
│ 235       ┆ 9.99999e5         ┆ 9.99999e5         ┆ 9.99999e5          ┆ 99999.0           │
└───────────┴───────────────────┴───────────────────┴────────────────────┴───────────────────┘,
    _body=<great_tables._gt_data.Body object at 0x000002485641B520>,
    _boxhead=Boxhead([ColInfo(var='_row_num_', type=<ColInfoTypeEnum.default: 1>, column_label='', column_align='right', column_width='33.4px'), ColInfo(var='G227_IPAQ_VIG_MET', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_MET</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='143px'), ColInfo(var='G227_IPAQ_MOD_MET', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_MOD_MET</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='143px'), ColInfo(var='G227_IPAQ_WALK_MET', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_WALK_MET</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='150px'), ColInfo(var='G227_IPAQ_TOT_MET', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_TOT_MET</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='143px')]),
    _stub=<great_tables._gt_data.Stub object at 0x000002485685FE30>,
    _spanners=Spanners([]),
    _heading=Heading(
        title=Md(
            text="<p>Report for Validation Step 7<div style='font-size: 13.6px; '><div style='padding-top: 7px;'>ASSERTION <span style='border-style: solid; border-width: thin; border-color: lightblue; padding-left: 2px; padding-right: 2px;'><code style='color: #303030; background-color: transparent; position: relative; bottom: 1px;'><code style='color: #303030; font-family: monos

In [37]:
validation.get_step_report(i=8, columns_subset=pb.matches(r"VIG"))

GT(
    _tbl_data=shape: (1, 7)
┌───────────┬──────────────┬──────────────┬──────────────┬─────────────┬─────────────┬─────────────┐
│ _row_num_ ┆ G227_IPAQ_VI ┆ G227_IPAQ_VI ┆ G227_IPAQ_VI ┆ G227_IPAQ_V ┆ G227_IPAQ_V ┆ G227_IPAQ_V │
│ ---       ┆ G_W          ┆ G_HPD        ┆ G_MPD        ┆ IG_D        ┆ IG_MINS     ┆ IG_MET      │
│ u32       ┆ ---          ┆ ---          ┆ ---          ┆ ---         ┆ ---         ┆ ---         │
│           ┆ f64          ┆ f64          ┆ f64          ┆ f64         ┆ f64         ┆ f64         │
╞═══════════╪══════════════╪══════════════╪══════════════╪═════════════╪═════════════╪═════════════╡
│ 471       ┆ 1.0          ┆ null         ┆ null         ┆ 999.0       ┆ 0.0         ┆ 0.0         │
└───────────┴──────────────┴──────────────┴──────────────┴─────────────┴─────────────┴─────────────┘,
    _body=<great_tables._gt_data.Body object at 0x000002485648FD90>,
    _boxhead=Boxhead([ColInfo(var='_row_num_', type=<ColInfoTypeEnum.default: 1>, column_label='', column_align='right', column_width='33.4px'), ColInfo(var='G227_IPAQ_VIG_W', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_W</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='127px'), ColInfo(var='G227_IPAQ_VIG_HPD', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_HPD</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='143px'), ColInfo(var='G227_IPAQ_VIG_MPD', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_MPD</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='143px'), ColInfo(var='G227_IPAQ_VIG_D', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_D</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='127px'), ColInfo(var='G227_IPAQ_VIG_MINS', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_MINS</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='150px'), ColInfo(var='G227_IPAQ_VIG_MET', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_MET</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='143px')]),
    _stub=<great_tables._gt_data.Stub object at 0x0000024853DEC6B0>,
    _spanners=Spanners([]),
    _heading=Heading(
        title=Md(
            text="<p>Report for Validation Step 8<div style='font-size: 13.6px; '><div style='padding-top: 7px;'>ASSERTION <span style='border-style: solid; border-width: thin; border-color: lightblue; padding-left: 2px; padding-right: 2px;'><code st

In [38]:
validation.get_step_report(i=9, columns_subset=pb.matches(r"VIG"))

GT(
    _tbl_data=shape: (10, 7)
┌───────────┬──────────────┬──────────────┬──────────────┬─────────────┬─────────────┬─────────────┐
│ _row_num_ ┆ G227_IPAQ_VI ┆ G227_IPAQ_VI ┆ G227_IPAQ_VI ┆ G227_IPAQ_V ┆ G227_IPAQ_V ┆ G227_IPAQ_V │
│ ---       ┆ G_W          ┆ G_HPD        ┆ G_MPD        ┆ IG_D        ┆ IG_MINS     ┆ IG_MET      │
│ u32       ┆ ---          ┆ ---          ┆ ---          ┆ ---         ┆ ---         ┆ ---         │
│           ┆ f64          ┆ f64          ┆ f64          ┆ f64         ┆ f64         ┆ f64         │
╞═══════════╪══════════════╪══════════════╪══════════════╪═════════════╪═════════════╪═════════════╡
│ 7         ┆ 1.0          ┆ null         ┆ 30.0         ┆ 4.0         ┆ 30.0        ┆ 960.0       │
│ 10        ┆ 1.0          ┆ null         ┆ 30.0         ┆ 1.0         ┆ 30.0        ┆ 240.0       │
│ 11        ┆ 1.0          ┆ null         ┆ 30.0         ┆ 1.0         ┆ 30.0        ┆ 240.0       │
│ 12        ┆ 1.0          ┆ null         ┆ null         ┆ 5.0         ┆ 0.0         ┆ 0.0         │
│ 16        ┆ 1.0          ┆ null         ┆ 30.0         ┆ 3.0         ┆ 30.0        ┆ 720.0       │
│ 23        ┆ 1.0          ┆ null         ┆ 10.0         ┆ 3.0         ┆ 10.0        ┆ 240.0       │
│ 30        ┆ 1.0          ┆ null         ┆ 30.0         ┆ 4.0         ┆ 30.0        ┆ 960.0       │
│ 31        ┆ 1.0          ┆ null         ┆ null         ┆ 3.0         ┆ 0.0         ┆ 0.0         │
│ 36        ┆ 1.0          ┆ null         ┆ 30.0         ┆ 1.0         ┆ 30.0        ┆ 240.0       │
│ 39        ┆ 1.0          ┆ null         ┆ 45.0         ┆ 2.0         ┆ 45.0        ┆ 720.0       │
└───────────┴──────────────┴──────────────┴──────────────┴─────────────┴─────────────┴─────────────┘,
    _body=<great_tables._gt_data.Body object at 0x0000024855478050>,
    _boxhead=Boxhead([ColInfo(var='_row_num_', type=<ColInfoTypeEnum.default: 1>, column_label='', column_align='right', column_width='25.6px'), ColInfo(var='G227_IPAQ_VIG_W', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_W</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='127px'), ColInfo(var='G227_IPAQ_VIG_HPD', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_HPD</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='143px'), ColInfo(var='G227_IPAQ_VIG_MPD', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_MPD</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='143px'), ColInfo(var='G227_IPAQ_VIG_D', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_D</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='127px'), ColInfo(var='G227_IPAQ_VIG_MINS', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_MINS</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; m

In [39]:
validation.get_step_report(i=10, columns_subset=pb.matches(r"VIG"))

GT(
    _tbl_data=shape: (10, 7)
┌───────────┬──────────────┬──────────────┬──────────────┬─────────────┬─────────────┬─────────────┐
│ _row_num_ ┆ G227_IPAQ_VI ┆ G227_IPAQ_VI ┆ G227_IPAQ_VI ┆ G227_IPAQ_V ┆ G227_IPAQ_V ┆ G227_IPAQ_V │
│ ---       ┆ G_W          ┆ G_HPD        ┆ G_MPD        ┆ IG_D        ┆ IG_MINS     ┆ IG_MET      │
│ u32       ┆ ---          ┆ ---          ┆ ---          ┆ ---         ┆ ---         ┆ ---         │
│           ┆ f64          ┆ f64          ┆ f64          ┆ f64         ┆ f64         ┆ f64         │
╞═══════════╪══════════════╪══════════════╪══════════════╪═════════════╪═════════════╪═════════════╡
│ 6         ┆ 1.0          ┆ 1.0          ┆ null         ┆ 1.0         ┆ 60.0        ┆ 480.0       │
│ 12        ┆ 1.0          ┆ null         ┆ null         ┆ 5.0         ┆ 0.0         ┆ 0.0         │
│ 14        ┆ 1.0          ┆ 1.0          ┆ null         ┆ 2.0         ┆ 60.0        ┆ 960.0       │
│ 15        ┆ 1.0          ┆ 10.0         ┆ null         ┆ 4.0         ┆ 600.0       ┆ 5760.0      │
│ 17        ┆ 1.0          ┆ 1.0          ┆ null         ┆ 3.0         ┆ 60.0        ┆ 1440.0      │
│ 18        ┆ 1.0          ┆ 5.0          ┆ null         ┆ 5.0         ┆ 300.0       ┆ 7200.0      │
│ 27        ┆ 1.0          ┆ 2.0          ┆ null         ┆ 6.0         ┆ 120.0       ┆ 5760.0      │
│ 28        ┆ 1.0          ┆ 1.0          ┆ null         ┆ 6.0         ┆ 60.0        ┆ 2880.0      │
│ 29        ┆ 1.0          ┆ 1.0          ┆ null         ┆ 2.0         ┆ 60.0        ┆ 960.0       │
│ 31        ┆ 1.0          ┆ null         ┆ null         ┆ 3.0         ┆ 0.0         ┆ 0.0         │
└───────────┴──────────────┴──────────────┴──────────────┴─────────────┴─────────────┴─────────────┘,
    _body=<great_tables._gt_data.Body object at 0x0000024855804370>,
    _boxhead=Boxhead([ColInfo(var='_row_num_', type=<ColInfoTypeEnum.default: 1>, column_label='', column_align='right', column_width='25.6px'), ColInfo(var='G227_IPAQ_VIG_W', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_W</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='127px'), ColInfo(var='G227_IPAQ_VIG_HPD', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_HPD</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='143px'), ColInfo(var='G227_IPAQ_VIG_MPD', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_MPD</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='143px'), ColInfo(var='G227_IPAQ_VIG_D', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_D</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='127px'), ColInfo(var='G227_IPAQ_VIG_MINS', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_MINS</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; m

In [40]:
validation.get_step_report(i=11, columns_subset=pb.matches(r"VIG"))

GT(
    _tbl_data=shape: (6, 7)
┌───────────┬──────────────┬──────────────┬──────────────┬─────────────┬─────────────┬─────────────┐
│ _row_num_ ┆ G227_IPAQ_VI ┆ G227_IPAQ_VI ┆ G227_IPAQ_VI ┆ G227_IPAQ_V ┆ G227_IPAQ_V ┆ G227_IPAQ_V │
│ ---       ┆ G_W          ┆ G_HPD        ┆ G_MPD        ┆ IG_D        ┆ IG_MINS     ┆ IG_MET      │
│ u32       ┆ ---          ┆ ---          ┆ ---          ┆ ---         ┆ ---         ┆ ---         │
│           ┆ f64          ┆ f64          ┆ f64          ┆ f64         ┆ f64         ┆ f64         │
╞═══════════╪══════════════╪══════════════╪══════════════╪═════════════╪═════════════╪═════════════╡
│ 8         ┆ 1.0          ┆ 4.0          ┆ 0.0          ┆ 1.0         ┆ 240.0       ┆ 1440.0      │
│ 15        ┆ 1.0          ┆ 10.0         ┆ null         ┆ 4.0         ┆ 600.0       ┆ 5760.0      │
│ 18        ┆ 1.0          ┆ 5.0          ┆ null         ┆ 5.0         ┆ 300.0       ┆ 7200.0      │
│ 26        ┆ 1.0          ┆ 4.0          ┆ 0.0          ┆ 6.0         ┆ 240.0       ┆ 8640.0      │
│ 62        ┆ 1.0          ┆ 4.0          ┆ null         ┆ 2.0         ┆ 240.0       ┆ 2880.0      │
│ 440       ┆ 1.0          ┆ 4.0          ┆ 0.0          ┆ 4.0         ┆ 240.0       ┆ 5760.0      │
└───────────┴──────────────┴──────────────┴──────────────┴─────────────┴─────────────┴─────────────┘,
    _body=<great_tables._gt_data.Body object at 0x0000024856584F50>,
    _boxhead=Boxhead([ColInfo(var='_row_num_', type=<ColInfoTypeEnum.default: 1>, column_label='', column_align='right', column_width='33.4px'), ColInfo(var='G227_IPAQ_VIG_W', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_W</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='127px'), ColInfo(var='G227_IPAQ_VIG_HPD', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_HPD</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='143px'), ColInfo(var='G227_IPAQ_VIG_MPD', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_MPD</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='143px'), ColInfo(var='G227_IPAQ_VIG_D', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_D</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='127px'), ColInfo(var='G227_IPAQ_VIG_MINS', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_MINS</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='150px'), ColInfo(var='G227_IPAQ_VIG_MET', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_MET</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidde

In [42]:
validation.get_step_report(i=12, columns_subset=pb.matches(r"ID|VIG"))

GT(
    _tbl_data=shape: (10, 8)
┌───────────┬─────────┬────────────┬────────────┬────────────┬────────────┬────────────┬───────────┐
│ _row_num_ ┆ ID      ┆ G227_IPAQ_ ┆ G227_IPAQ_ ┆ G227_IPAQ_ ┆ G227_IPAQ_ ┆ G227_IPAQ_ ┆ G227_IPAQ │
│ ---       ┆ ---     ┆ VIG_W      ┆ VIG_HPD    ┆ VIG_MPD    ┆ VIG_D      ┆ VIG_MINS   ┆ _VIG_MET  │
│ u32       ┆ f64     ┆ ---        ┆ ---        ┆ ---        ┆ ---        ┆ ---        ┆ ---       │
│           ┆         ┆ f64        ┆ f64        ┆ f64        ┆ f64        ┆ f64        ┆ f64       │
╞═══════════╪═════════╪════════════╪════════════╪════════════╪════════════╪════════════╪═══════════╡
│ 1         ┆ 10270.0 ┆ 0.0        ┆ null       ┆ null       ┆ 888.0      ┆ 0.0        ┆ 0.0       │
│ 2         ┆ 10280.0 ┆ 0.0        ┆ null       ┆ null       ┆ 888.0      ┆ 0.0        ┆ 0.0       │
│ 3         ┆ 10290.0 ┆ 0.0        ┆ null       ┆ null       ┆ 888.0      ┆ 0.0        ┆ 0.0       │
│ 4         ┆ 10390.0 ┆ 0.0        ┆ null       ┆ null       ┆ 888.0      ┆ 0.0        ┆ 0.0       │
│ 5         ┆ 10430.0 ┆ 0.0        ┆ null       ┆ null       ┆ 888.0      ┆ 0.0        ┆ 0.0       │
│ 6         ┆ 10440.0 ┆ 0.0        ┆ null       ┆ null       ┆ 888.0      ┆ 0.0        ┆ 0.0       │
│ 7         ┆ 10460.0 ┆ 0.0        ┆ null       ┆ null       ┆ 888.0      ┆ 0.0        ┆ 0.0       │
│ 8         ┆ 10660.0 ┆ 0.0        ┆ null       ┆ null       ┆ 888.0      ┆ 0.0        ┆ 0.0       │
│ 9         ┆ 10820.0 ┆ 0.0        ┆ null       ┆ null       ┆ 888.0      ┆ 0.0        ┆ 0.0       │
│ 10        ┆ 11080.0 ┆ 0.0        ┆ null       ┆ null       ┆ 888.0      ┆ 0.0        ┆ 0.0       │
└───────────┴─────────┴────────────┴────────────┴────────────┴────────────┴────────────┴───────────┘,
    _body=<great_tables._gt_data.Body object at 0x000002485573C140>,
    _boxhead=Boxhead([ColInfo(var='_row_num_', type=<ColInfoTypeEnum.default: 1>, column_label='', column_align='right', column_width='25.6px'), ColInfo(var='ID', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>ID</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='65px'), ColInfo(var='G227_IPAQ_VIG_W', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_W</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='127px'), ColInfo(var='G227_IPAQ_VIG_HPD', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_HPD</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='143px'), ColInfo(var='G227_IPAQ_VIG_MPD', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_MPD</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='143px'), ColInfo(var='G227_IPAQ_VIG_D', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_D</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em>

In [44]:
validation.get_step_report(i=35, columns_subset=pb.matches(r"ID|_D|MINS|MET|CAT"))

GT(
    _tbl_data=shape: (10, 13)
┌───────────┬─────────┬────────────┬───────────┬───┬───────────┬───────────┬───────────┬───────────┐
│ _row_num_ ┆ ID      ┆ G227_IPAQ_ ┆ G227_IPAQ ┆ … ┆ G227_IPAQ ┆ G227_IPAQ ┆ G227_IPAQ ┆ G227_IPAQ │
│ ---       ┆ ---     ┆ VIG_D      ┆ _VIG_MINS ┆   ┆ _MOD_MET  ┆ _WALK_MET ┆ _TOT_MET  ┆ _CAT      │
│ u32       ┆ f64     ┆ ---        ┆ ---       ┆   ┆ ---       ┆ ---       ┆ ---       ┆ ---       │
│           ┆         ┆ f64        ┆ f64       ┆   ┆ f64       ┆ f64       ┆ f64       ┆ f64       │
╞═══════════╪═════════╪════════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪═══════════╡
│ 1         ┆ 10020.0 ┆ 1.0        ┆ 20.0      ┆ … ┆ 0.0       ┆ 792.0     ┆ 952.0     ┆ 0.0       │
│ 2         ┆ 10100.0 ┆ 3.0        ┆ 150.0     ┆ … ┆ 840.0     ┆ 693.0     ┆ 5133.0    ┆ 1.0       │
│ 3         ┆ 10150.0 ┆ 1.0        ┆ 60.0      ┆ … ┆ 240.0     ┆ 165.0     ┆ 885.0     ┆ 0.0       │
│ 7         ┆ 10230.0 ┆ 4.0        ┆ 30.0      ┆ … ┆ 480.0     ┆ 495.0     ┆ 1935.0    ┆ 1.0       │
│ 8         ┆ 10250.0 ┆ 1.0        ┆ 240.0     ┆ … ┆ 0.0       ┆ 4158.0    ┆ 5598.0    ┆ 1.0       │
│ 10        ┆ 10280.0 ┆ 888.0      ┆ 0.0       ┆ … ┆ 0.0       ┆ 1485.0    ┆ 1485.0    ┆ 0.0       │
│ 11        ┆ 10290.0 ┆ 888.0      ┆ 0.0       ┆ … ┆ 3600.0    ┆ 2970.0    ┆ 6570.0    ┆ 1.0       │
│ 12        ┆ 10310.0 ┆ 3.0        ┆ 60.0      ┆ … ┆ 480.0     ┆ 3465.0    ┆ 5385.0    ┆ 1.0       │
│ 13        ┆ 10340.0 ┆ 1.0        ┆ 30.0      ┆ … ┆ 0.0       ┆ 396.0     ┆ 636.0     ┆ 0.0       │
│ 18        ┆ 10430.0 ┆ 888.0      ┆ 0.0       ┆ … ┆ 640.0     ┆ 1386.0    ┆ 2026.0    ┆ 1.0       │
└───────────┴─────────┴────────────┴───────────┴───┴───────────┴───────────┴───────────┴───────────┘,
    _body=<great_tables._gt_data.Body object at 0x0000024856FA0460>,
    _boxhead=Boxhead([ColInfo(var='_row_num_', type=<ColInfoTypeEnum.default: 1>, column_label='', column_align='right', column_width='25.6px'), ColInfo(var='ID', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>ID</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='65px'), ColInfo(var='G227_IPAQ_VIG_D', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_D</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='127px'), ColInfo(var='G227_IPAQ_VIG_MINS', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_VIG_MINS</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='150px'), ColInfo(var='G227_IPAQ_MOD_D', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_MOD_D</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64</em></div></div>"), column_align='right', column_width='127px'), ColInfo(var='G227_IPAQ_MOD_MINS', type=<ColInfoTypeEnum.default: 1>, column_label=Html(text="<div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-bottom: 2px; margin-bottom: 2px;'>G227_IPAQ_MOD_MINS</div><div style='white-space: nowrap; text-overflow: ellipsis; overflow: hidden; padding-top: 2px; margin-top: 2px;'><em>Float64

In [ ]:
df.filter(
    pl.col("ID").is_in([10020, 12900]),
    # pl.col("^.*IPAQ")
)

shape: (2, 23)
┌─────────┬────────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬───────────┐
│ ID      ┆ G227_IPAQ_ ┆ G227_IPAQ ┆ G227_IPAQ ┆ … ┆ G227_IPAQ ┆ G227_IPAQ ┆ G227_IPAQ ┆ G227_IPAQ │
│ ---     ┆ VIG_W      ┆ _VIG_HPD  ┆ _VIG_MPD  ┆   ┆ _MOD_MET  ┆ _WALK_MET ┆ _TOT_MET  ┆ _CAT      │
│ f64     ┆ ---        ┆ ---       ┆ ---       ┆   ┆ ---       ┆ ---       ┆ ---       ┆ ---       │
│         ┆ f64        ┆ f64       ┆ f64       ┆   ┆ f64       ┆ f64       ┆ f64       ┆ f64       │
╞═════════╪════════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪═══════════╡
│ 10020.0 ┆ 1.0        ┆ 0.0       ┆ 20.0      ┆ … ┆ 0.0       ┆ 792.0     ┆ 952.0     ┆ 0.0       │
│ 12900.0 ┆ 1.0        ┆ 3.0       ┆ null      ┆ … ┆ 2880.0    ┆ 990.0     ┆ 9630.0    ┆ 2.0       │
└─────────┴────────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴───────────┘

In [59]:
df.null_count()

shape: (1, 23)
┌─────┬────────────┬────────────┬────────────┬───┬────────────┬────────────┬───────────┬───────────┐
│ ID  ┆ G227_IPAQ_ ┆ G227_IPAQ_ ┆ G227_IPAQ_ ┆ … ┆ G227_IPAQ_ ┆ G227_IPAQ_ ┆ G227_IPAQ ┆ G227_IPAQ │
│ --- ┆ VIG_W      ┆ VIG_HPD    ┆ VIG_MPD    ┆   ┆ MOD_MET    ┆ WALK_MET   ┆ _TOT_MET  ┆ _CAT      │
│ u32 ┆ ---        ┆ ---        ┆ ---        ┆   ┆ ---        ┆ ---        ┆ ---       ┆ ---       │
│     ┆ u32        ┆ u32        ┆ u32        ┆   ┆ u32        ┆ u32        ┆ u32       ┆ u32       │
╞═════╪════════════╪════════════╪════════════╪═══╪════════════╪════════════╪═══════════╪═══════════╡
│ 0   ┆ 0          ┆ 686        ┆ 848        ┆ … ┆ 0          ┆ 0          ┆ 0         ┆ 0         │
└─────┴────────────┴────────────┴────────────┴───┴────────────┴────────────┴───────────┴───────────┘